# Toric Decoder
Apply the [2D decoder](https://arxiv.org/abs/1406.2338), followed by [minimum-weight perfect matching](https://arxiv.org/abs/2303.15933), on the toric code with side length $L$. We consider i.i.d. $X$ errors on the qubits (bonds), and work with $m$ anyons (plaquettes). The errors are plotted on the dual lattice by default.
## 2D Decoder
At each time step out of $T=L$ total, perform the following steps:
1. Make an $X$ error on each qubit with probability $p=0.05$.
2. Perform $c$ field updates, according to the following rule:$$\phi\mapsto\phi+\frac\eta4\nabla^2\phi+q$$Where $\phi$ is the auxillary field, $\eta=0.1$ is the Jacobi smoothing parameter, and $q$ is the anyon density with unit mass $-\frac4\eta$. Take $4\pi G=1$, so that $\nabla^2\phi=\rho$.
3. For each anyon, move it its highest-$\phi$ neighboring cell with probability $\frac12$.

## Notebook Initialization

In [1]:
%matplotlib widget

In [2]:
import numpy as np
import matplotlib.pyplot as plt

import seaborn as sns
mako = sns.color_palette("mako", as_cmap=True)

plt.rcParams["animation.html"] = "jshtml"
plt.rcParams['figure.dpi'] = 150
plt.ioff()

from tqdm.notebook import tqdm
import os
import sys
from multiprocess import Pool
try:
    num_cpus = len(os.sched_getaffinity(0))
    sys.path.insert(0, 'toric-decoder')
except:
    num_cpus = os.cpu_count()
print("Using {} CPUs".format(num_cpus))

from toric import *
from pymatching import Matching

Using 4 CPUs


## Example

In [3]:
# Simulation parameters

L = 100 # Lattice size
p_error = 0.05 # Error probability per spin
η = 0.1 # Smoothing paramter for Jacobi method
c = 16 # "Field velocity" - number of field updates per cycle
T = L # Epochs

matching = Matching(pcm(L))

In [4]:
mystate = init_state(L)
mystate.add_errors(p_error)
initial_correction = mwpm(matching, mystate.q)
print("Fail after MWPM: {}".format(logical_error(initial_correction ^ mystate.error)))

q_history, error_history = decoder_2D_history(mystate, T, c, η, p_error = 0)
print("Fail after 2D: {}".format(mystate.N > 0 or logical_error(mystate.error)))

correction = mwpm(matching, q_history[-1,:,:])
q_history = np.append(q_history, [np.zeros_like(mystate.q)], axis = 0)
error_history = np.append(error_history, [mystate.error ^ correction], axis = 0)
print("Fail after 2D and MWPM: {}".format(logical_error(error_history[-1,:,:,:])))

Fail after MWPM: False
Fail after 2D: True
Fail after 2D and MWPM: False


In [5]:
plot_evolution(q_history, error_history, dual = True)

## JIT Benchmarking
### Parameter Space
* System size $L=100$
* Field velocity $c=16$
* Error rate per $\tau$ time steps: $p=0.05$, $\tau=1$
* Time steps $T=L$
* Smoothing factor $\eta=0.1$
* Shots: $10$
### Recorded Data
* Failure rate
* Anyon density
### Results
| Method | Time   | Speedup |
| ------ | ------ | ------- |
| NumPy  | 55.3 s | 1.00    |
| Numba  | 15.6 s | 3.54    |
| 4 CPUs | 5.82 s | 9.50    |

## PyMatching Benchmarking
### Parameter Space
* System size $L\in\{100,200,400\}$
* Error rate $p\in\{0.01,0.05,0.20\}$
* Shots: 100

In [7]:
L = 400

In [8]:
%timeit m = Matching(pcm(L))

165 ms ± 17.2 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [13]:
p = 0.2
# Allow for JIT compilation
m = Matching(pcm(L))
state = init_state(L)
state.add_errors(p)
corr = mwpm(m, state.q)
fail = logical_error(corr ^ state.error)

In [ ]:
%%timeit
pass
state = init_state(L)
state.add_errors(p)
corr = mwpm(m, state.q)
fail = logical_error(corr ^ state.error)

54 ms ± 525 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)
